In [1]:
import pandas as pd
import numpy as np
import warnings 
import nltk
import matplotlib.pyplot as plt
from nltk.tokenize import RegexpTokenizer
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import word_tokenize
import re
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import LatentDirichletAllocation
from sklearn.model_selection import train_test_split
from gensim.models import LdaModel
from gensim.models.coherencemodel import CoherenceModel
from gensim import corpora
from gensim.corpora import Dictionary
from datetime import datetime

In [2]:
import pyLDAvis
import pyLDAvis.gensim_models

In [3]:
warnings.filterwarnings('ignore')

In [4]:
#data =  pd.read_csv('data_processed.csv',  engine = 'python',  on_bad_lines = 'skip', index_col=[0])

In [5]:
data =  pd.read_csv('data_processed.csv',  engine = 'python',  on_bad_lines = 'skip')

In [6]:
data.columns

Index(['Id', 'Title', 'Title_tokens', 'Body', 'Body_tokens', 'Tags',
       'Tag_token', 'Score', 'AnswerCount'],
      dtype='object')

In [7]:
data.shape

(50000, 9)

In [8]:
X = data[['Title_tokens', 'Body_tokens','Tag_token','Score', 'AnswerCount']]
y = data[['Tag_token']]

# re tokenisations des variables tockens suite à la lecture csv qui lit champe en string,  mise à jour aussi dans dataframe data. 
X['Title_tokens'] = X['Title_tokens'].apply(lambda x: re.sub('[^a-zA-Z_]', ' ', str(x)))
X['Title_tokens'] = X['Title_tokens'].apply(nltk.word_tokenize)
X['Body_tokens'] = X['Body_tokens'].apply(lambda x: re.sub('[^a-zA-Z_]', ' ', str(x)))
X['Body_tokens'] = X['Body_tokens'].apply(nltk.word_tokenize)
X['Tag_token'] = X['Tag_token'].apply(lambda x: re.sub('[^a-zA-Z_]', ' ', str(x)))
X['Tag_token'] = X['Tag_token'].apply(nltk.word_tokenize)

# Split the Title_tokens into train and test sets
X_train, X_test = train_test_split(X, test_size=0.2, random_state=42)

X_train_title = X_train['Title_tokens']
X_test_title = X_test['Title_tokens']
X_train_body = X_train['Body_tokens']
X_test_body = X_test['Body_tokens']
X_train_tag = X_train['Tag_token']
X_test_tag = X_test['Tag_token']

In [9]:
X_train_title.head()

39087                                  [stored, procedure]
30893                         [run, fly, tomcat, netbeans]
45278    [show, gray, color, view, navigation, bar, uis...
16398       [authentication, ticket, decryption, possible]
13653                                    [validation, yii]
Name: Title_tokens, dtype: object

In [10]:
X_test_tag.head()

33553         [javascript, jquery, html, css, tablesorter]
9427               [php, mysql, file, codeigniter, upload]
199      [python, python, x, csv, dictionary, multidime...
12447               [php, net, frameworks, ldap, openldap]
39489    [vue, js, vuejs, datepicker, vue, component, v...
Name: Tag_token, dtype: object

# 3. Modèles non supervisés

Nous utilisons LDA comme le modèle non supervisé.  LDA entrainé est utilisée pour découvrir des sujets cachés dans les nouveaux documents. 
Les mots les plus probables dans ces sujets découverts sont généralement considérés comme les mots-clés les plus pertinents pour le document.

In [11]:
performance_list = []
pyLDAvis.enable_notebook()

# 3.1 Entrainement et nombre de topics

In [12]:
def lda_train(num_topics, X_train):
    # Create a dictionary and bag-of-words representation of the training data
    dictionary = Dictionary(X_train)
    bow_corpus = [dictionary.doc2bow(doc) for doc in X_train]
    
    # Train the LDA model
    lda_model = LdaModel(corpus=bow_corpus, num_topics=num_topics, id2word=dictionary)

    topics = lda_model.get_document_topics(bow_corpus)
    
    #  Visulisation des topics 
#    vis = pyLDAvis.gensim_models.prepare(topic_model=lda_model, corpus=bow_corpus, dictionary=dictionary, mds='mmds', R=30)
    vis = pyLDAvis.gensim_models.prepare(topic_model=lda_model, corpus=bow_corpus, dictionary=dictionary, mds='pcoa', sort_topics=True)
    
    # Calculer la perplexité
    perplexity = lda_model.log_perplexity(bow_corpus)

    # Calculer la cohérence des topics
    coherence_model = CoherenceModel(model=lda_model, texts=X_train, corpus=bow_corpus, coherence='c_v')
    coherence_score = coherence_model.get_coherence()
    
    return perplexity, coherence_score, lda_model, vis

### 3.1.1 Modèle 1: LDA entrainement avec titre

In [13]:
num_topics = 10
perplexity_titre, coherence_score_titre, lda_titre, vis_titre = lda_train(num_topics, X_train_title)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre', num_topics, perplexity_titre, coherence_score_titre]
performance_list.append(y_resultat)
vis_titre

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
2     -0.158618 -0.096571       1        1  11.132990
7      0.159870  0.069178       2        1  10.861957
4      0.103954 -0.101460       3        1  10.486211
8     -0.031868  0.181344       4        1  10.326659
6     -0.140408 -0.213384       5        1  10.050998
0      0.200345 -0.013856       6        1   9.995431
3     -0.099576 -0.066814       7        1   9.962094
5     -0.087034  0.260179       8        1   9.404390
1      0.206598 -0.066964       9        1   9.244288
9     -0.153263  0.048348      10        1   8.534982, topic_info=           Term        Freq       Total Category  logprob  loglift
30       column  627.000000  627.000000  Default  30.0000  30.0000
224      button  653.000000  653.000000  Default  29.0000  29.0000
64     variable  583.000000  583.000000  Default  28.0000  28.0000
71       spring  684.000000  684.000000  Default  27.0000  27.0000
173        ajax  520.000000  520.000000  Default  26.0000  26.0000
..          ...         ...         ...      ...      ...      ...
545  controller  141.292328  312.535304  Topic10  -4.7094   1.6671
6           bar  119.307934  218.615384  Topic10  -4.8785   1.8554
755       issue  113.968621  602.607237  Topic10  -4.9243   0.7957
295        make  107.977259  564.612756  Topic10  -4.9783   0.8068
366        item  102.086933  315.479394  Topic10  -5.0344   1.3327

[595 rows x 6 columns], token_table=      Topic      Freq     Term
term                          
797       2  0.093243   access
797       3  0.277561   access
797       4  0.002168   access
797       6  0.080232   access
797       7  0.021684   access
...     ...       ...      ...
308       4  0.015629      xml
308       6  0.214894      xml
308       8  0.015629      xml
308      10  0.134797      xml
1242      7  0.991419  youtube

[1395 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[3, 8, 5, 9, 7, 1, 4, 6, 2, 10])

In [14]:
num_topics = 15
perplexity_titre, coherence_score_titre, lda_titre, vis_titre = lda_train(num_topics, X_train_title)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre', num_topics, perplexity_titre, coherence_score_titre]
performance_list.append(y_resultat)
vis_titre

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
2      0.062169 -0.035477       1        1  7.385566
13    -0.037665  0.077968       2        1  7.219505
11     0.200427  0.034892       3        1  7.146546
0      0.206803 -0.062392       4        1  7.055573
12    -0.128235 -0.013858       5        1  6.971420
14    -0.048935  0.193021       6        1  6.924845
1     -0.159652  0.049847       7        1  6.770605
5     -0.204772 -0.125083       8        1  6.712457
9      0.171264  0.071408       9        1  6.655166
6     -0.007424 -0.230124      10        1  6.406272
7     -0.061349  0.072669      11        1  6.405269
3      0.051576 -0.198648      12        1  6.232401
4      0.026292  0.203586      13        1  6.183806
10    -0.135345  0.005347      14        1  6.022217
8      0.064846 -0.043155      15        1  5.908353, topic_info=          Term        Freq       Total Category  logprob  loglift
330     custom  738.000000  738.000000  Default  30.0000  30.0000
71      spring  759.000000  759.000000  Default  29.0000  29.0000
30      column  684.000000  684.000000  Default  28.0000  28.0000
64    variable  644.000000  644.000000  Default  27.0000  27.0000
528     return  596.000000  596.000000  Default  26.0000  26.0000
...        ...         ...         ...      ...      ...      ...
956        new  339.485926  464.720339  Topic15  -3.4650   2.5148
273       long  131.362632  171.122159  Topic15  -4.4145   2.5644
662      match  104.443633  129.025017  Topic15  -4.6438   2.6174
610      login  122.976423  227.216628  Topic15  -4.4804   2.2149
1555     graph  106.562622  153.983621  Topic15  -4.6237   2.4607

[735 rows x 6 columns], token_table=      Topic      Freq       Term
term                            
741       9  0.981179       able
797       2  0.975471     access
797      11  0.011969     access
797      14  0.009974     access
539       7  0.987134  accessing
...     ...       ...        ...
308       8  0.001753        xml
308      11  0.099916        xml
308      15  0.001753        xml
18        5  0.986877        yii
1242     11  0.987225    youtube

[1642 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[3, 14, 12, 1, 13, 15, 2, 6, 10, 7, 8, 4, 5, 11, 9])

In [15]:
num_topics = 20
perplexity_titre, coherence_score_titre, lda_titre, vis_titre = lda_train(num_topics, X_train_title)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre', num_topics, perplexity_titre, coherence_score_titre]
performance_list.append(y_resultat)
vis_titre

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
1      0.093106 -0.078117       1        1  5.698880
19     0.029101 -0.013530       2        1  5.536830
7      0.096402  0.191598       3        1  5.475639
17    -0.149902 -0.003915       4        1  5.469089
14    -0.084435  0.001667       5        1  5.294818
18     0.108470 -0.006570       6        1  5.213538
0      0.006652 -0.104855       7        1  5.174577
15    -0.038348 -0.185970       8        1  5.144669
11     0.128237 -0.068948       9        1  5.108147
3     -0.248343  0.054879      10        1  5.096495
4     -0.078070 -0.182768      11        1  5.045307
13     0.070137  0.187592      12        1  5.013070
9     -0.255154  0.107659      13        1  4.984002
16     0.038469  0.038683      14        1  4.856040
12     0.114386  0.020650      15        1  4.801276
5      0.065821  0.154252      16        1  4.762350
2      0.043729 -0.162729      17        1  4.428068
8     -0.035218  0.008361      18        1  4.384564
6      0.086704 -0.017808      19        1  4.356586
10     0.008255  0.059869      20        1  4.156055, topic_info=           Term        Freq       Total Category  logprob  loglift
25        query  688.000000  688.000000  Default  30.0000  30.0000
71       spring  777.000000  777.000000  Default  29.0000  29.0000
370        type  663.000000  663.000000  Default  28.0000  28.0000
295        make  650.000000  650.000000  Default  27.0000  27.0000
330      custom  706.000000  706.000000  Default  26.0000  26.0000
...         ...         ...         ...      ...      ...      ...
295        make  619.416211  650.576825  Topic20  -2.5119   3.1315
210       point  190.853145  197.230612  Topic20  -3.6891   3.1477
525         top  113.495621  117.818897  Topic20  -4.2089   3.1432
608     cordova   76.715597   79.781735  Topic20  -4.6005   3.1414
1334  typeerror   66.988134   70.088616  Topic20  -4.7361   3.1354

[881 rows x 6 columns], token_table=      Topic      Freq       Term
term                            
797       1  0.982336     access
797      17  0.004018     access
797      18  0.004018     access
797      19  0.006027     access
539       4  0.987723  accessing
...     ...       ...        ...
308      17  0.003573        xml
308      18  0.001787        xml
308      19  0.141142        xml
18        5  0.983417        yii
1242     16  0.983479    youtube

[1746 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[2, 20, 8, 18, 15, 19, 1, 16, 12, 4, 5, 14, 10, 17, 13, 6, 3, 9, 7, 11])

In [16]:
num_topics = 30
perplexity_titre, coherence_score_titre, lda_titre, vis_titre = lda_train(num_topics, X_train_title)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre', num_topics, perplexity_titre, coherence_score_titre]
performance_list.append(y_resultat)
vis_titre

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
6     -0.167496  0.041159       1        1  3.989793
3      0.087589  0.002194       2        1  3.892976
11    -0.147274  0.051400       3        1  3.865544
23    -0.015442 -0.054117       4        1  3.758612
10     0.185415  0.193438       5        1  3.658806
14    -0.123180  0.065796       6        1  3.587516
1     -0.135976  0.052826       7        1  3.571361
19     0.068007  0.135682       8        1  3.565460
17    -0.116060  0.091082       9        1  3.518045
4      0.039456 -0.110385      10        1  3.494900
13    -0.007210 -0.042490      11        1  3.492046
2      0.127256  0.101350      12        1  3.459905
9      0.107481 -0.023538      13        1  3.443569
26    -0.028851 -0.059355      14        1  3.442634
27    -0.078907 -0.040417      15        1  3.411250
0      0.015954 -0.094983      16        1  3.401175
20     0.083191 -0.020462      17        1  3.283420
25    -0.114481  0.030910      18        1  3.260792
12     0.005351 -0.115632      19        1  3.254346
15     0.155288  0.004792      20        1  3.145175
24     0.080353  0.157578      21        1  3.118310
16     0.046932 -0.166209      22        1  3.096963
18    -0.075286  0.108962      23        1  3.061707
28     0.054852 -0.185713      24        1  3.004395
5      0.012911  0.011872      25        1  2.975181
22     0.004802 -0.063588      26        1  2.973115
29     0.001035  0.041030      27        1  2.971964
8     -0.067736 -0.062655      28        1  2.810584
21     0.048510 -0.035188      29        1  2.806511
7     -0.046484 -0.015338      30        1  2.683946, topic_info=           Term        Freq       Total Category  logprob  loglift
370        type  684.000000  684.000000  Default  30.0000  30.0000
30       column  700.000000  700.000000  Default  29.0000  29.0000
25        query  697.000000  697.000000  Default  28.0000  28.0000
66      element  654.000000  654.000000  Default  27.0000  27.0000
432   different  686.000000  686.000000  Default  26.0000  26.0000
...         ...         ...         ...      ...      ...      ...
1797      agent   42.091157   43.199104  Topic30  -4.7635   3.5919
1447      small   53.102476   54.569565  Topic30  -4.5311   3.5906
218          cs  426.793433  464.601819  Topic30  -2.4471   3.5330
1923        pop   50.099818   51.627524  Topic30  -4.5893   3.5878
1017      token  215.838464  249.127872  Topic30  -3.1288   3.4744

[1088 rows x 6 columns], token_table=      Topic      Freq     Term
term                          
741      19  0.982757     able
797       4  0.971757   access
797      13  0.002008   access
797      14  0.010039   access
797      15  0.012047   access
...     ...       ...      ...
308      30  0.001750      xml
1999     19  0.983891    xpath
18       23  0.974219      yii
1242     11  0.985577  youtube
1644      7  0.971878     zoom

[1663 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[7, 4, 12, 24, 11, 15, 2, 20, 18, 5, 14, 3, 10, 27, 28, 1, 21, 26, 13, 16, 25, 17, 19, 29, 6, 23, 30, 9, 22, 8])

In [17]:
num_topics = 50
perplexity_titre, coherence_score_titre, lda_titre, vis_titre = lda_train(num_topics, X_train_title)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre', num_topics, perplexity_titre, coherence_score_titre]
performance_list.append(y_resultat)
vis_titre

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
38     0.035799 -0.043714       1        1  2.666731
46     0.051172 -0.100280       2        1  2.652525
2      0.017961 -0.034843       3        1  2.520924
11     0.036808 -0.005974       4        1  2.453011
25    -0.015268 -0.028455       5        1  2.433657
47     0.057758  0.010093       6        1  2.408615
13     0.008425 -0.013103       7        1  2.397482
20    -0.003534 -0.016610       8        1  2.375375
41    -0.021914 -0.029081       9        1  2.335572
23     0.022875  0.005355      10        1  2.301555
43     0.011897 -0.025422      11        1  2.300368
1      0.019467 -0.041298      12        1  2.185790
24     0.011328 -0.008603      13        1  2.171457
0      0.016001 -0.001548      14        1  2.168118
19     0.084931  0.332248      15        1  2.167468
29     0.007726 -0.022099      16        1  2.160078
8      0.020769 -0.023229      17        1  2.157093
34     0.023769 -0.019097      18        1  2.117540
32    -0.342167  0.055084      19        1  2.082482
30     0.011271 -0.024443      20        1  2.069233
12     0.012866 -0.040225      21        1  2.031663
7      0.024906  0.030586      22        1  2.027326
48     0.003697 -0.015727      23        1  2.004793
33     0.023755 -0.041216      24        1  2.000171
40     0.000434 -0.015416      25        1  1.973794
18     0.036383  0.007302      26        1  1.972290
17     0.009540 -0.006518      27        1  1.903570
37     0.016369 -0.010751      28        1  1.891357
31     0.009754 -0.011980      29        1  1.886929
49     0.004177 -0.011606      30        1  1.868504
26     0.003679 -0.005667      31        1  1.864043
10     0.005926 -0.000503      32        1  1.858281
22     0.009538 -0.016234      33        1  1.846364
5      0.072701  0.305915      34        1  1.833828
42     0.009123 -0.011211      35        1  1.818236
4      0.032921 -0.077757      36        1  1.814779
3      0.011132 -0.021218      37        1  1.803269
45     0.007550 -0.009626      38        1  1.787697
39    -0.117272  0.009314      39        1  1.756618
15     0.005776 -0.008947      40        1  1.754282
36     0.001132 -0.011035      41        1  1.737503
9      0.010412 -0.019852      42        1  1.691742
44    -0.298789  0.058437      43        1  1.686121
35     0.011845 -0.011459      44        1  1.669680
16     0.023144  0.000226      45        1  1.648688
27     0.004703 -0.011829      46        1  1.622030
28     0.002232  0.000718      47        1  1.595674
14     0.004656 -0.012028      48        1  1.523914
6      0.004513 -0.006932      49        1  1.514769
21    -0.001880  0.000258      50        1  1.487010, topic_info=            Term        Freq       Total Category  logprob  loglift
330       custom  820.000000  820.000000  Default  30.0000  30.0000
71        spring  795.000000  795.000000  Default  29.0000  29.0000
370         type  715.000000  715.000000  Default  28.0000  28.0000
12          view  677.000000  677.000000  Default  27.0000  27.0000
432    different  685.000000  685.000000  Default  26.0000  26.0000
...          ...         ...         ...      ...      ...      ...
495    protected   27.010093   28.169348  Topic50  -4.6166   4.1664
1940      picker   26.148948   27.303872  Topic50  -4.6490   4.1652
2406  relational   18.185444   19.340367  Topic50  -5.0122   4.1468
2118      mocked   17.861716   19.016640  Topic50  -5.0302   4.1457
2220   slideshow   16.713797   17.868721  Topic50  -5.0966   4.1416

[1570 rows x 6 columns], token_table=      Topic      Freq      Term
term                           
741      36  0.980038      able
1762     36  0.980509  absolute
419       3  0.936465    accept
797       5  0.001981    access
797      17  0.992685    access
...     ...       ...       ...
18        3  0.979459       yii
1242     34  0.986570   youtube
2395     45  0.983058      

### 3.1.2 Modèle 2: LDA entrainement avec titre + body

In [18]:
X_train_merged = X_train_title + X_train_body

In [19]:
X_train_merged.head()

39087    [stored, procedure, calling, stored, procedure...
30893    [run, fly, tomcat, netbeans, maven, web, proje...
45278    [show, gray, color, view, navigation, bar, uis...
16398    [authentication, ticket, decryption, possible,...
13653    [validation, yii, validation, yii, advanced, p...
dtype: object

In [20]:
X_train_title.head()

39087                                  [stored, procedure]
30893                         [run, fly, tomcat, netbeans]
45278    [show, gray, color, view, navigation, bar, uis...
16398       [authentication, ticket, decryption, possible]
13653                                    [validation, yii]
Name: Title_tokens, dtype: object

In [21]:
X_train_body.head()

39087    [calling, stored, procedure, execute, procedur...
30893    [maven, web, project, netbeans, eclipse, refer...
45278    [written, test, ipad, contains, split, view, u...
16398    [php, developer, almost, nothing, net, asked, ...
13653    [validation, yii, advanced, parent_id, creatin...
Name: Body_tokens, dtype: object

In [22]:
num_topics = 10
perplexity_merged, coherence_score_merged, lda_merged, vis_merged = lda_train(num_topics, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre et body', num_topics, perplexity_merged, coherence_score_merged]
performance_list.append(y_resultat)
vis_merged

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
8      0.083092  0.046555       1        1  15.585489
9      0.153821  0.043387       2        1  12.641126
2      0.119775 -0.183355       3        1  12.127953
7     -0.019479 -0.028530       4        1  11.475160
0     -0.046555 -0.091955       5        1  11.390148
1     -0.108442  0.045560       6        1   9.150824
3     -0.223210  0.090389       7        1   9.075402
5     -0.098979 -0.034501       8        1   8.809585
6     -0.014658 -0.064357       9        1   6.215207
4      0.154635  0.176808      10        1   3.529105, topic_info=        Term         Freq        Total Category  logprob  loglift
35      test  6104.000000  6104.000000  Default  30.0000  30.0000
122    image  7931.000000  7931.000000  Default  29.0000  29.0000
180    table  6729.000000  6729.000000  Default  28.0000  28.0000
189   column  4623.000000  4623.000000  Default  27.0000  27.0000
749   button  5520.000000  5520.000000  Default  26.0000  26.0000
...      ...          ...          ...      ...      ...      ...
629    field   361.297037  3745.702005  Topic10  -5.2481   1.0055
40       add   368.851826  5357.495259  Topic10  -5.2274   0.6683
1319     xml   325.646183  3639.564060  Topic10  -5.3520   0.9303
999    based   309.300113  2980.760423  Topic10  -5.4035   1.0785
401     list   307.768643  5363.456850  Topic10  -5.4084   0.4861

[821 rows x 6 columns], token_table=      Topic      Freq  Term
term                       
393       1  0.146933  able
393       2  0.089933  able
393       3  0.121388  able
393       4  0.096477  able
393       5  0.104922  able
...     ...       ...   ...
3008      5  0.017314  zone
3008      7  0.005771  zone
939       3  0.003146  zoom
939       5  0.006292  zoom
939       9  0.987879  zoom

[3344 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[9, 10, 3, 8, 1, 2, 4, 6, 7, 5])

In [23]:
num_topics = 20
perplexity_merged, coherence_score_merged, lda_merged, vis_merged = lda_train(num_topics, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre et body', num_topics, perplexity_merged, coherence_score_merged]
performance_list.append(y_resultat)
pyLDAvis.display(vis_merged)

In [24]:
num_topics = 30
perplexity_merged, coherence_score_merged, lda_merged, vis_merged = lda_train(num_topics, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre et body', num_topics, perplexity_merged, coherence_score_merged]
performance_list.append(y_resultat)
pyLDAvis.display(vis_merged)

In [25]:
num_topics = 50
perplexity_merged, coherence_score_merged, lda_merged, vis_merged = lda_train(num_topics, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre et body', num_topics, perplexity_merged, coherence_score_merged]
performance_list.append(y_resultat)
pyLDAvis.display(vis_merged)

Nous sélectionnons le model avec 20 topics avec titre

### 3.1.3  Modèle 3: LDA entrainement avec titre & tag et body

In [26]:
def lda_train_tag(num_topics, dictionary, X_train):
    # Create a dictionary and bag-of-words representation of the training data
    # dictionary = Dictionary(X_train)
    bow_corpus = [dictionary.doc2bow(doc) for doc in X_train]
    
    # Train the LDA model
    lda_model = LdaModel(corpus=bow_corpus, num_topics=num_topics, id2word=dictionary)

    topics = lda_model.get_document_topics(bow_corpus)
    
    #  Visulisation des topics 
#    vis = pyLDAvis.gensim_models.prepare(topic_model=lda_model, corpus=bow_corpus, dictionary=dictionary, mds='mmds', R=30)
    vis = pyLDAvis.gensim_models.prepare(topic_model=lda_model, corpus=bow_corpus, dictionary=dictionary, mds='pcoa', sort_topics=True)
    
    # Calculer la perplexité
    perplexity = lda_model.log_perplexity(bow_corpus)

    # Calculer la cohérence des topics
    coherence_model = CoherenceModel(model=lda_model, texts=X_train, corpus=bow_corpus, coherence='c_v')
    coherence_score = coherence_model.get_coherence()
    
    return perplexity, coherence_score, lda_model, vis

In [27]:
# Create a set of tokens from X_train_title and X_train_tag
title_tokens_set = set([token for tokens in X_train_title for token in tokens])
tag_tokens_set = set([token for tokens in X_train_tag for token in tokens])

# Get the common tokens that appear in both sets
X_train_union = title_tokens_set.intersection(tag_tokens_set)

train_dictionary_tag = Dictionary([list(X_train_union)])

In [28]:
num_topics = 10
perplexity_tag, coherence_score_tag, lda_tag, vis_tag = lda_train_tag(num_topics, train_dictionary_tag, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre&tag + body', num_topics, perplexity_tag, coherence_score_tag]
performance_list.append(y_resultat)
pyLDAvis.display(vis_tag)

In [29]:
num_topics = 20
perplexity_tag, coherence_score_tag, lda_tag, vis_tag = lda_train_tag(num_topics, train_dictionary_tag, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre&tag + body', num_topics, perplexity_tag, coherence_score_tag]
performance_list.append(y_resultat)
pyLDAvis.display(vis_tag)

In [30]:
num_topics = 30
perplexity_tag, coherence_score_tag, lda_tag, vis_tag = lda_train_tag(num_topics, train_dictionary_tag, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre&tag + body', num_topics, perplexity_tag, coherence_score_tag]
performance_list.append(y_resultat)
pyLDAvis.display(vis_tag)

In [31]:
num_topics = 50
perplexity_tag, coherence_score_tag, lda_tag, vis_tag = lda_train_tag(num_topics, train_dictionary_tag, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre&tag + body', num_topics, perplexity_tag, coherence_score_tag]
performance_list.append(y_resultat)
pyLDAvis.display(vis_tag)

In [32]:
train_result = pd.DataFrame(performance_list, columns=['Date', 'Modele', 'nb topics', 'perplexity', 'coherence_score'])
train_result.to_csv('lda_train_result.csv')

### 3.1.4 LDA entrainement avec titre pour fit et titre+body pour transform

In Gensim, the topic modeling models such as LdaModel do not have separate fit and transform methods like in some other machine learning libraries. Instead, the training and transformation steps are combined into a single process.

### 3.1.5 Example des topics découverts 

In [33]:
num_topics = 10

In [34]:
# Create a dictionary and bag-of-words representation of the training data, modèle 1: 
train_dictionary = Dictionary(X_train_title)
train_bow_corpus = [train_dictionary.doc2bow(doc) for doc in X_train_title]

# Train LDA model with 20 topics
lda_model = LdaModel(corpus=train_bow_corpus, num_topics=num_topics, id2word=train_dictionary)

# topics distribution pour chaque docuement dans X_train_title
train_topics_distribution = lda_model.get_document_topics(train_bow_corpus)

In [35]:
# les 10 topics découverts avec les 8 top words
topics = lda_model.print_topics(num_words=8)
for topic in topics:
    words = topic[1].split('+')
    words = [word.split('*')[1].replace('"', '').strip() for word in words]
    print(words)

['issue', 'rail', 'module', 'import', 'performance', 'template', 'validation', 'side']
['column', 'show', 'row', 'property', 'another', 'null', 'panda', 'dataframe']
['loop', 'type', 'select', 'specific', 'return', 'parameter', 'plugin', 'used']
['date', 'django', 'convert', 'test', 'output', 'trying', 'insert', 'project']
['variable', 'getting', 'memory', 'read', 'http', 'line', 'found', 'find']
['different', 'spring', 'query', 'studio', 'visual', 'core', 'single', 'two']
['view', 'call', 'framework', 'mvc', 'react', 'system', 'controller', 'default']
['service', 'inside', 'post', 'request', 'map', 'send', 'model', 'azure']
['button', 'display', 'xml', 'click', 'element', 'event', 'attribute', 'remove']
['url', 'ajax', 'best', 'load', 'selenium', 'folder', 'token', 'mobile']


In [36]:
# afficher les probailité des topics des documents
for i in range(2):
    print(f"Document {i+1} topic distribution:")
    for topic, prob in train_topics_distribution[i]:
        print(f"Topic {topic}: {prob}")
    print()

Document 1 topic distribution:
Topic 0: 0.033333923667669296
Topic 1: 0.6999945640563965
Topic 2: 0.033333923667669296
Topic 3: 0.03333396837115288
Topic 4: 0.033333923667669296
Topic 5: 0.03333395719528198
Topic 6: 0.033333923667669296
Topic 7: 0.033333923667669296
Topic 8: 0.033333923667669296
Topic 9: 0.033333923667669296

Document 2 topic distribution:
Topic 0: 0.02000763826072216
Topic 1: 0.2802756726741791
Topic 2: 0.020004427060484886
Topic 3: 0.5596908330917358
Topic 4: 0.020003993064165115
Topic 5: 0.020003359764814377
Topic 6: 0.020003365352749825
Topic 7: 0.02000381238758564
Topic 8: 0.020003458485007286
Topic 9: 0.020003441721200943



## 3.2 prédiction de topics et les mots

In [37]:
def predit_word(num_topics, X_train, X_test):
    # Prédict la topics distribution for each document in the test set X_test_title
    train_dictionary = Dictionary(X_train)
    train_bow_corpus = [train_dictionary.doc2bow(doc) for doc in X_train]
    
    # Train the LDA model
    lda_model = LdaModel(corpus=train_bow_corpus, num_topics=num_topics, id2word=train_dictionary)
    
    # création bow pour X_test_title avec les dictionary train  (avec test_body et option)    
    test_bow_corpus = [train_dictionary.doc2bow(doc) for doc in X_test]
    test_topics_distributions = lda_model[test_bow_corpus] 
    
    # Extract keywords from the inferred topic distributions
    test_keywords = []
    for doc_topics in test_topics_distributions:       
    # trier les topics par la probailité en order décroissant (x[1] de doc_topics)
        sorted_topics = sorted(doc_topics, key=lambda x: x[1], reverse=True)
    # extraire le premier mot clé des top topics 
        top_keywords = [train_dictionary[word_id] for word_id, _ in sorted_topics[:10]]  # Adjust the number of keywords as needed
        test_keywords.append(top_keywords)
    return test_keywords

### 3.2.1 Prediction avec modèle 1 

In [38]:
num_topics = 20

In [39]:
test_keywords_m1 = predit_word(num_topics, X_train_title, X_test_title)

In [40]:
print(test_keywords_m1[:5])

[['authentication', 'stored', 'procedure', 'fly', 'netbeans', 'run', 'tomcat', 'bar', 'color', 'gray'], ['authentication', 'navigation', 'tomcat', 'possible', 'procedure', 'stored', 'fly', 'netbeans', 'run', 'bar'], ['authentication', 'decryption', 'procedure', 'stored', 'fly', 'netbeans', 'run', 'tomcat', 'bar', 'color'], ['show', 'certain', 'uisplitviewcontroller', 'decryption', 'procedure', 'stored', 'fly', 'netbeans', 'run', 'tomcat'], ['authentication', 'procedure', 'navigation', 'yii', 'stored', 'fly', 'netbeans', 'run', 'tomcat', 'bar']]


### 3.2.2 Prediction avec modèle 2 

In [41]:
num_topics = 30

In [42]:
test_keywords_m2 = predit_word(num_topics, X_train_title + X_train_body,  X_test_title + X_test_body)

In [43]:
print(test_keywords_m2[:5])

[['net', 'project', 'parameter', 'goal', 'return', 'stored', 'sql'], ['stored', 'eclipse', 'correct', 'project', 'parameter', 'go', 'chose', 'passing'], ['eclipse', 'directly', 'project', 'although', 'passing', 'copy', 'fine'], ['sql', 'procedure', 'maven', 'although', 'project', 'parameter', 'correct', 'calling'], ['go', 'parameter', 'possibility']]


### 3.2.2 Prediction avec modèle 3

In [44]:
def predit_word_tag(num_topics, train_dictionary, X_train, X_test):
    # Prédict la topics distribution for each document in the test set X_test_title
    # train_dictionary = Dictionary(X_train)
    train_bow_corpus = [train_dictionary.doc2bow(doc) for doc in X_train]
    
    # Train the LDA model
    lda_model = LdaModel(corpus=train_bow_corpus, num_topics=num_topics, id2word=train_dictionary)
    
    # création bow pour X_test_title avec les dictionary train  (avec test_body et option)    
    test_bow_corpus = [train_dictionary.doc2bow(doc) for doc in X_test]
    test_topics_distributions = lda_model[test_bow_corpus] 
    
    # Extract keywords from the inferred topic distributions
    test_keywords = []
    for doc_topics in test_topics_distributions:       
    # trier les topics par la probailité en order décroissant (x[1] de doc_topics)
        sorted_topics = sorted(doc_topics, key=lambda x: x[1], reverse=True)
    # extraire le premier mot clé des top topics 
        top_keywords = [train_dictionary[word_id] for word_id, _ in sorted_topics[:10]]  # Adjust the number of keywords as needed
        test_keywords.append(top_keywords)
    return test_keywords

In [45]:
# Create a set of tokens from X_train_title and X_train_tag
title_tokens_set = set([token for tokens in X_train_title for token in tokens])
tag_tokens_set = set([token for tokens in X_train_tag for token in tokens])

# Get the common tokens that appear in both sets
X_train_union = title_tokens_set.intersection(tag_tokens_set)

train_dictionary_tag = Dictionary([list(X_train_union)])

In [46]:
num_topics = 10

In [47]:
test_keywords_m3 = predit_word_tag(num_topics, train_dictionary_tag, X_train_title, X_test_title)

In [48]:
print(test_keywords_m3[:5])

[['aar', 'acceleration', 'abstraction', 'aac', 'absolute', 'accelerometer', 'abstract', 'abi', 'abide', 'abort'], ['aac', 'acceleration', 'aar', 'accelerometer', 'abi', 'abide', 'abstraction', 'abort', 'absolute', 'abstract'], ['aac', 'abstraction', 'absolute', 'accelerometer', 'aar', 'abort', 'acceleration', 'abi', 'abide', 'abstract'], ['acceleration', 'abi', 'abstract', 'abort', 'aac', 'abide', 'absolute', 'abstraction', 'accelerometer', 'aar'], ['abstraction', 'abort', 'absolute', 'accelerometer', 'aac', 'acceleration', 'aar', 'abi', 'abstract', 'abide']]


## 3.3 Mesure de prediction

In [49]:
def prediction_couverture(predits, reels): 

    # Convertir les colonnes des dataframes en listes de tokens
    mots_cles_reels = reels.tolist()  # convert token to list de strings
    mots_cles_predits = predits

    # Compteur de mots clés réels correctement prédits
    mots_cles_corrects = 0

    # Parcourir les mots clés réels
    for mots_reels in mots_cles_reels:  # pour chaque document
        for mot_reel in mots_reels:     # chaque mot reel du document
        # si un mot réel est parmi les mots prédits
            if any(mot_reel in mots_predits for mots_predits in mots_cles_predits):
                mots_cles_corrects += 1
                break

    # Calculer le taux de couverture des tags réels
    taux_couverture = mots_cles_corrects / len(mots_cles_reels) * 100

    # Afficher le taux de couverture des tags réels
    print("Taux de couverture des tags réels :", taux_couverture, "%")
    return taux_couverture

In [496]:
couverture_m1 = prediction_couverture(test_keywords_m1,X_test['Tag_token'])

Taux de couverture des tags réels : 4.04 %


In [497]:
couverture_m2 = prediction_couverture(test_keywords_m2,X_test['Tag_token'])

Taux de couverture des tags réels : 18.240000000000002 %


In [526]:
couverture_m3 = prediction_couverture(test_keywords_m3,X_test['Tag_token'])

Taux de couverture des tags réels : 0.2 %


## 3.1 Détermination de nombre optimal de sujets

LDA est utilisée pour découvrir des sujets cachés dans les documents. Chaque document est une distribution de sujets et chaque sujet est une distribution de mots. Si le nombre de sujets est trop élevé, le modèle peut surajuster les données d'apprentissage, Overffiting et créer des sujets non informatiques.   Si le nombre de sujets est trop faible, il y a perte d'information,  des sujets trop généraux et manque de différenciation. D'où la nécessité de cherche un nombre optimal. 

In [143]:
X_train_title = X_train['Title_tokens']
X_test_title = X_test['Title_tokens']
X_train_body = X_train['Body_tokens']
X_test_body = X_test['Body_tokens']

In [144]:
def find_topics_number(X_train):
    # Préparer le dictionnaire
    dictionary = Dictionary(X_train)

    # Convertir le corpus en une représentation vectorielle (sac de mots)
    train_bow = [dictionary.doc2bow(doc) for doc in X_train]

    # Diviser le corpus en ensembles d'apprentissage et de validation
    
    train_corpus, val_corpus = train_test_split(train_bow, test_size=0.2, random_state=42)
    print(' train bow size =', len(train_corpus), 'val size =', len(val_corpus))
    
    # Liste pour stocker les perplexités
    perplexities = []

    # Nombre de sujets à évaluer
    num_topics_list = [5, 10, 20, 30, 40, 50, 100, 200]

    # Entraîner les modèles LDA et calculer les perplexités
    for num_topics in num_topics_list:
        lda_model = LdaModel(train_corpus, num_topics=num_topics, id2word=dictionary)
#        perplexity = lda_model.log_perplexity(val_corpus)
        perplexity = lda_model.log_perplexity(train_corpus)
        perplexities.append(perplexity)
        print(f"Nombre de sujets : {num_topics}, Perplexité : {perplexity}")

    # Trouver le nombre optimal de sujets avec la perplexité la plus faible
    optimal_num_topics = num_topics_list[perplexities.index(min(perplexities))]
    return optimal_num_topics


In [145]:
num_topics_title = find_topics_number(X_train_title)

 train bow size = 32000 val size = 8000
Nombre de sujets : 5, Perplexité : -8.160909831711681
Nombre de sujets : 10, Perplexité : -8.685802974307766
Nombre de sujets : 20, Perplexité : -11.356819447490578
Nombre de sujets : 30, Perplexité : -12.996426544618757
Nombre de sujets : 40, Perplexité : -14.840559456344964
Nombre de sujets : 50, Perplexité : -17.216560859801607
Nombre de sujets : 100, Perplexité : -60.47661051331654
Nombre de sujets : 200, Perplexité : -398.8067932128906


In [146]:
def find_optimal_num_topics(X_train):
    # Préparer le dictionnaire
    dictionary = Dictionary(X_train)

    # Convertir le corpus en une représentation vectorielle (sac de mots)
    train_bow = [dictionary.doc2bow(doc) for doc in X_train]    
    
    # Nombre de sujets à évaluer
    num_topics_list = [5, 10, 20, 30, 40, 50, 100, 200]
    
    perplexities = []
    coherence_scores = []

    for num_topics in num_topics_list:
        # Entraîner le modèle LDA
        lda_model = LdaModel(train_bow, num_topics=num_topics, id2word=dictionary)

        # Calculer la perplexité
        perplexity = lda_model.log_perplexity(train_bow)
        perplexities.append(perplexity)

        # Calculer la cohérence des topics
        coherence_model = CoherenceModel(model=lda_model, texts=X_train, corpus=train_bow, coherence='c_v')
        coherence_score = coherence_model.get_coherence()
        coherence_scores.append(coherence_score)

        print(f"Nombre de sujets : {num_topics}, Perplexité : {perplexity}, Cohérence : {coherence_score}")

    # Trouver le nombre optimal de sujets en utilisant une approche combinée
    combined_scores = [p + c for p, c in zip(perplexities, coherence_scores)]
    optimal_num_topics = num_topics_list[combined_scores.index(min(combined_scores))]

    return optimal_num_topics


In [147]:
# Utilisation de la fonction find_optimal_num_topics pour trouver le nombre optimal de sujets
optimal_num_topics = find_optimal_num_topics(X_train_title)
optimal_num_topics


Nombre de sujets : 5, Perplexité : -8.147663929077003, Cohérence : 0.33433522067570903
Nombre de sujets : 10, Perplexité : -8.645684040670103, Cohérence : 0.3847911297048994
Nombre de sujets : 20, Perplexité : -11.377812485437072, Cohérence : 0.4580272427163691
Nombre de sujets : 30, Perplexité : -13.040845536825808, Cohérence : 0.527198120661385
Nombre de sujets : 40, Perplexité : -14.8449386442342, Cohérence : 0.575516915328435
Nombre de sujets : 50, Perplexité : -17.286233070830484, Cohérence : 0.5953587928565621
Nombre de sujets : 100, Perplexité : -56.353362749362816, Cohérence : 0.4734337966651315
Nombre de sujets : 200, Perplexité : -384.4603310254296, Cohérence : 0.7985812298104998


200

In [825]:
print(X_train_title[:100])

39087                                  [stored, procedure]
30893                              [fly, tomcat, netbeans]
45278                 [show, gray, color, navigation, bar]
16398       [authentication, ticket, decryption, possible]
13653                                    [validation, yii]
                               ...                        
49622                            [drawing, uiview, iphone]
41140    [program, mouseover, control, divs, larger, de...
11416                                           [backbone]
35988                               [implementation, ruby]
498                        [hide, taskbar, taking, screen]
Name: Title_tokens, Length: 100, dtype: object


In [842]:
from sklearn.model_selection import KFold

def find_optimal_num_topics_cross_validation(X_train, num_folds=5):
    
    # Nombre de sujets à évaluer
    num_topics_list = [5, 10, 20, 40, 100]
    
    # Diviser le corpus en K plis
    kf = KFold(n_splits=num_folds, shuffle=True, random_state=42)
    
    perplexities = []
    coherence_scores = []
    
    for num_topics in num_topics_list:
        fold_perplexities = []
        fold_coherence_scores = []
        
        for train_index, val_index in kf.split(X_train):
        # Diviser le corpus en ensembles d'apprentissage et de validation
            X_train_fold = X_train.iloc[train_index].values.tolist()
            X_val_fold = X_train.iloc[val_index].values.tolist()
            
            # Préparer le dictionnaire
            dictionary = Dictionary(X_train_fold)
            
            # Convertir le corpus en une représentation vectorielle (sac de mots)
            train_bow = [dictionary.doc2bow(doc) for doc in X_train_fold]
            val_bow = [dictionary.doc2bow(doc) for doc in X_val_fold]
            
            # Entraîner le modèle LDA
            lda_model = LdaModel(train_bow, num_topics=num_topics, id2word=dictionary)
            
            # Calculer la perplexité
            perplexity = lda_model.log_perplexity(val_bow)
            fold_perplexities.append(perplexity)
            
            # Calculer la cohérence des topics
            coherence_model = CoherenceModel(model=lda_model, texts=X_train_fold, corpus=train_bow, coherence='c_v')
            coherence_score = coherence_model.get_coherence()
            fold_coherence_scores.append(coherence_score)
        
        # Calculer les moyennes des perplexités et des scores de cohérence sur les plis
        mean_perplexity = sum(fold_perplexities) / num_folds
        mean_coherence = sum(fold_coherence_scores) / num_folds
        
        perplexities.append(mean_perplexity)
        coherence_scores.append(mean_coherence)
        
        print(f"Nombre de sujets : {num_topics}, Perplexité moyenne : {mean_perplexity}, Cohérence moyenne : {mean_coherence}")
    
    # Trouver le nombre optimal de sujets en utilisant une approche combinée
    combined_scores = [p + c for p, c in zip(perplexities, coherence_scores)]
    optimal_num_topics = num_topics_list[combined_scores.index(min(combined_scores))]
    
    return optimal_num_topics


In [843]:
optimal_num_topics = find_optimal_num_topics_cross_validation(X_train_title, 5)
print(f"Nombre optimal de sujets : {optimal_num_topics}")

Nombre de sujets : 5, Perplexité moyenne : -8.826589198606827, Cohérence moyenne : 0.5111803945771971
Nombre de sujets : 10, Perplexité moyenne : -9.402572921184712, Cohérence moyenne : 0.5300611538266922
Nombre de sujets : 20, Perplexité moyenne : -12.275141462642813, Cohérence moyenne : 0.5639125076950797
Nombre de sujets : 40, Perplexité moyenne : -16.36354027403153, Cohérence moyenne : 0.6273990263591562
Nombre de sujets : 100, Perplexité moyenne : -79.27656749624217, Cohérence moyenne : 0.5741283692792261
Nombre optimal de sujets : 100


In [ ]:
# Step 5: Evaluation

# Initialize variables to keep track of evaluation metrics
true_positives = 0
false_positives = 0
false_negatives = 0

# Iterate through each document in the test set
for i in range(len(test_documents)):
    # Get the extracted keywords for the current document
    extracted_keywords = top_keywords_per_document[i]

    # Get the ground truth keywords for the current document
    ground_truth_keywords = ground_truth_keywords_per_document[i]

    # Calculate the number of true positives, false positives, and false negatives
    for keyword in extracted_keywords:
        if keyword in ground_truth_keywords:
            true_positives += 1
        else:
            false_positives += 1

    for keyword in ground_truth_keywords:
        if keyword not in extracted_keywords:
            false_negatives += 1

# Calculate evaluation metrics
precision = true_positives / (true_positives + false_positives)
recall = true_positives / (true_positives + false_negatives)
f1_score = 2 * (precision * recall) / (precision + recall)
accuracy = (true_positives + true_negatives) / total_documents

# Print the evaluation metrics
print("Precision:", precision)
print("Recall:", recall)
print("F1-score:", f1_score)
print("Accuracy:", accuracy)


## 3.2 NMF + TF-IDF